Creating a choropleth map to visualise the changes in air quality.

In [1]:
import pandas as pd
import plotly.express as px
import os

# Load the data for each year (2017-2023)
files = {
    2017: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2017.csv',
    2018: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2018.csv',
    2019: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2019.csv',
    2020: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2020.csv',
    2021: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2021.csv',
    2022: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2022.csv',
    2023: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2023.csv'
}

# Read and prepare each dataset
dfs = []
for year, file_path in files.items():
    df = pd.read_csv(file_path)
    df = df[['State', 'County', 'Year', 'Median AQI']].rename(columns={'Median AQI': f'Median AQI {year}'})
    dfs.append(df)

# Merge all datasets on 'State' and 'County'
df_merged = dfs[0]
for df in dfs[1:]:
    df_merged = df_merged.merge(df, on=['State', 'County'], suffixes=('', '_drop'))
    df_merged.drop([col for col in df_merged.columns if 'drop' in col], axis=1, inplace=True)

# Mapping state names to their respective state abbreviations
state_abbrev = {
    'Alabama': 'AL', 'Alaska': 'AK', 'Arizona': 'AZ', 'Arkansas': 'AR',
    'California': 'CA', 'Colorado': 'CO', 'Connecticut': 'CT',
    'Delaware': 'DE', 'District Of Columbia': 'DC', 'Florida': 'FL',
    'Georgia': 'GA', 'Hawaii': 'HI', 'Idaho': 'ID', 'Illinois': 'IL',
    'Indiana': 'IN', 'Iowa': 'IA', 'Kansas': 'KS', 'Kentucky': 'KY',
    'Louisiana': 'LA', 'Maine': 'ME', 'Maryland': 'MD',
    'Massachusetts': 'MA', 'Michigan': 'MI', 'Minnesota': 'MN',
    'Mississippi': 'MS', 'Missouri': 'MO', 'Montana': 'MT',
    'Nebraska': 'NE', 'Nevada': 'NV', 'New Hampshire': 'NH',
    'New Jersey': 'NJ', 'New Mexico': 'NM', 'New York': 'NY',
    'North Carolina': 'NC', 'North Dakota': 'ND', 'Ohio': 'OH',
    'Oklahoma': 'OK', 'Oregon': 'OR', 'Pennsylvania': 'PA',
    'Rhode Island': 'RI', 'South Carolina': 'SC', 'South Dakota': 'SD',
    'Tennessee': 'TN', 'Texas': 'TX', 'Utah': 'UT', 'Vermont': 'VT',
    'Virginia': 'VA', 'Washington': 'WA', 'West Virginia': 'WV',
    'Wisconsin': 'WI', 'Wyoming': 'WY'
}

# Apply state abbreviation mapping
df_merged['State'] = df_merged['State'].map(state_abbrev)

# Combine the data for animation
df_combined = pd.concat(
    [
        df_merged[['State', 'County', f'Median AQI {year}']].rename(columns={f'Median AQI {year}': 'Median AQI'}).assign(Year=year)
        for year in range(2017, 2024)
    ]
)

# Create an animated choropleth map
animated_fig = px.choropleth(
    df_combined,
    locationmode="USA-states",
    locations="State",
    color="Median AQI",
    hover_name="County",
    hover_data=["Median AQI"],
    animation_frame="Year",
    scope="usa",
    title="Median AQI by County (2017-2023)",
    color_continuous_scale="Viridis"
)
# Save the animated choropleth map as HTML file in the current working directory
output_file = "animated_choropleth_map_2017_2023.html"
animated_fig.write_html(output_file)

# Provide the path to the saved HTML file
animated_html_path = os.path.abspath(output_file)
print(animated_html_path)

animated_fig.show()

/Users/clioluo/Desktop/Data Visualization/Final Project/animated_choropleth_map_2017_2023.html


Creating a symbol map to visualize the consumption of fuel for electricity generation.

In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# Load CSV files
file_paths = [
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2017.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2018.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2019.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2020.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2021.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2022.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2023.csv'
]

dfs = [pd.read_csv(file_path) for file_path in file_paths]

# Clean column names
dfs_cleaned = []
for df in dfs:
    df.columns = df.columns.str.strip().str.replace('\n', ' ')
    dfs_cleaned.append(df)

# Convert 'Elec Fuel Consumption MMBtu' to numeric and aggregate by 'Plant State'
def clean_and_aggregate(df):
    df['Elec Fuel Consumption MMBtu'] = df['Elec Fuel Consumption MMBtu'].str.replace(',', '').astype(float)
    aggregated = df.groupby('Plant State')['Elec Fuel Consumption MMBtu'].sum().reset_index()
    return aggregated

dfs_aggregated = [clean_and_aggregate(df) for df in dfs_cleaned]

# Add a year column to each DataFrame
for i, df in enumerate(dfs_aggregated):
    df['Year'] = 2017 + i

# Combine all years into one DataFrame
combined_df = pd.concat(dfs_aggregated, ignore_index=True)

# Check and fill missing states with zero consumption
all_states = pd.Series(pd.concat(dfs_aggregated)['Plant State'].unique())
all_years = pd.Series(range(2017, 2024))

# Create a DataFrame with all combinations of states and years
state_year_df = pd.MultiIndex.from_product([all_states, all_years], names=['Plant State', 'Year']).to_frame(index=False)

# Merge the combined data with the state-year DataFrame to fill missing states with zero consumption
combined_df_filled = state_year_df.merge(combined_df, on=['Plant State', 'Year'], how='left').fillna(0)
combined_df_filled['Elec Fuel Consumption MMBtu'] = combined_df_filled['Elec Fuel Consumption MMBtu'].astype(float)

# Create a basic scatter_geo plot
fig = px.scatter_geo(
    combined_df_filled,
    locations="Plant State",
    locationmode="USA-states",
    size="Elec Fuel Consumption MMBtu",
    animation_frame="Year",
    scope="usa",
    title='Changes in Electric Fuel Consumption (MMBtu) by State (2017-2023)',
    labels={'Elec Fuel Consumption MMBtu':'Fuel Consumption (MMBtu)'},
    color="Elec Fuel Consumption MMBtu",
    color_continuous_scale=px.colors.sequential.Plasma,
    hover_name="Plant State",  # Name to show on hover
    hover_data={"Elec Fuel Consumption MMBtu": True,  # Show consumption data
                "Year": True} 
)

# Add state boundaries to the map
fig.update_geos(fitbounds="locations", visible=False)

fig.add_trace(go.Choropleth(
    locations=combined_df['Plant State'].unique(),
    locationmode='USA-states',
    z=[0]*len(combined_df['Plant State'].unique()),
    showscale=False,
    geo='geo'
))

# Update layout to include fixed zoom level without automatic zooming
fig.update_geos(
    lataxis={"range": [20, 50]}, 
    lonaxis={"range": [-130, -60]}
)


import os
# Save the animated bubble map as an HTML file in the current working directory
output_file = "elec_fuel_consumption_animation.html"
fig.write_html(output_file)

fig.show()


Creating a dashboard.

In [3]:
#! pip install dash dash-bootstrap-components

In [ ]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from dash import Dash, dcc, html
import dash_bootstrap_components as dbc
import os

# Load CSV files for electric fuel consumption
file_paths = [
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2017.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2018.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2019.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2020.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2021.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2022.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2023.csv'
]

# Read CSV files into DataFrames
dfs = [pd.read_csv(file_path) for file_path in file_paths]

# Clean column names
dfs = [df.rename(columns=lambda x: x.strip().replace('\n', ' ')) for df in dfs]

# Convert 'Elec Fuel Consumption MMBtu' to numeric and aggregate by 'Plant State'
def clean_and_aggregate(df):
    df['Elec Fuel Consumption MMBtu'] = df['Elec Fuel Consumption MMBtu'].str.replace(',', '').astype(float)
    return df.groupby('Plant State')['Elec Fuel Consumption MMBtu'].sum().reset_index()

dfs = [clean_and_aggregate(df) for df in dfs]

# Add a year column to each DataFrame and combine all years into one DataFrame
for i, df in enumerate(dfs):
    df['Year'] = 2017 + i
combined_df = pd.concat(dfs, ignore_index=True)

# Ensure all state-year combinations are present, filling missing combinations with zero consumption
all_states = pd.Series(combined_df['Plant State'].unique())
all_years = pd.Series(range(2017, 2024))
state_year_df = pd.MultiIndex.from_product([all_states, all_years], names=['Plant State', 'Year']).to_frame(index=False)

combined_df_filled = state_year_df.merge(combined_df, on=['Plant State', 'Year'], how='left').fillna(0)
combined_df_filled['Elec Fuel Consumption MMBtu'] = combined_df_filled['Elec Fuel Consumption MMBtu'].astype(float)

# Create a basic scatter_geo plot
bubble_map_fig = px.scatter_geo(
    combined_df_filled,
    locations="Plant State",
    locationmode="USA-states",
    size="Elec Fuel Consumption MMBtu",
    animation_frame="Year",
    scope="usa",
    title='Changes in Electric Fuel Consumption (MMBtu) by State (2017-2023)',
    labels={'Elec Fuel Consumption MMBtu':'Fuel Consumption (MMBtu)'},
    color="Elec Fuel Consumption MMBtu",
    color_continuous_scale=px.colors.sequential.Plasma,
    hover_name="Plant State",
    hover_data={
        'Plant State': True,
        'Elec Fuel Consumption MMBtu': ':.0f',
        'Year': True} 
)

# Add state boundaries to the map
bubble_map_fig.update_geos(fitbounds="locations", visible=False)

bubble_map_fig.add_trace(go.Choropleth(
    locations=combined_df['Plant State'].unique(),
    locationmode='USA-states',
    z=[0]*len(combined_df['Plant State'].unique()),
    showscale=False,
    geo='geo'
))

# Update layout to include a fixed zoom level without automatic zooming
bubble_map_fig.update_geos(
    lataxis={"range": [20, 50]}, 
    lonaxis={"range": [-130, -60]}
)

# Save the bubble map figure as an HTML file
bubble_map_fig.write_html('/Users/clioluo/Desktop/Data Visualization/Final Project/bubble_map.html')

# Load AQI data for each year (2017-2023)
files = {
    2017: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2017.csv',
    2018: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2018.csv',
    2019: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2019.csv',
    2020: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2020.csv',
    2021: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2021.csv',
    2022: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2022.csv',
    2023: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2023.csv'
}

# Read and prepare each dataset
dfs = []
for year, file_path in files.items():
    if os.path.exists(file_path):
        df = pd.read_csv(file_path)
        df = df[['State', 'County', 'Year', 'Median AQI']].rename(columns={'Median AQI': f'Median AQI {year}'})
        dfs.append(df)
    else:
        print(f"File not found: {file_path}")

# Ensure dfs is not empty before attempting to merge
if dfs:
    # Merge all datasets on 'State' and 'County'
    df_merged = dfs[0]
    for df in dfs[1:]:
        df_merged = df_merged.merge(df, on=['State', 'County'], suffixes=('', '_drop'))
        df_merged.drop([col for col in df_merged.columns if 'drop' in col], axis=1, inplace=True)
else:
    raise ValueError("No dataframes were loaded. Check the file paths.")

# Mapping state names to their respective state abbreviations
state_abbrev = {
    'Alabama': 'AL', 'Alaska': 'AK', 'Arizona': 'AZ', 'Arkansas': 'AR',
    'California': 'CA', 'Colorado': 'CO', 'Connecticut': 'CT',
    'Delaware': 'DE', 'District Of Columbia': 'DC', 'Florida': 'FL',
    'Georgia': 'GA', 'Hawaii': 'HI', 'Idaho': 'ID', 'Illinois': 'IL',
    'Indiana': 'IN', 'Iowa': 'IA', 'Kansas': 'KS', 'Kentucky': 'KY',
    'Louisiana': 'LA', 'Maine': 'ME', 'Maryland': 'MD',
    'Massachusetts': 'MA', 'Michigan': 'MI', 'Minnesota': 'MN',
    'Mississippi': 'MS', 'Missouri': 'MO', 'Montana': 'MT',
    'Nebraska': 'NE', 'Nevada': 'NV', 'New Hampshire': 'NH',
    'New Jersey': 'NJ', 'New Mexico': 'NM', 'New York': 'NY',
    'North Carolina': 'NC', 'North Dakota': 'ND', 'Ohio': 'OH',
    'Oklahoma': 'OK', 'Oregon': 'OR', 'Pennsylvania': 'PA',
    'Rhode Island': 'RI', 'South Carolina': 'SC', 'South Dakota': 'SD',
    'Tennessee': 'TN', 'Texas': 'TX', 'Utah': 'UT', 'Vermont': 'VT',
    'Virginia': 'VA', 'Washington': 'WA', 'West Virginia': 'WV',
    'Wisconsin': 'WI', 'Wyoming': 'WY'
}

# Apply state abbreviation mapping
df_merged['State'] = df_merged['State'].map(state_abbrev)

# Combine the data for animation
aqi_combined_df = pd.concat(
    [
        df_merged[['State', 'County', f'Median AQI {year}']].rename(columns={f'Median AQI {year}': 'Median AQI'}).assign(Year=year)
        for year in range(2017, 2024)
    ]
)

# Create an animated choropleth map
choropleth_map_fig = px.choropleth(
    aqi_combined_df,
    locationmode="USA-states",
    locations="State",
    color="Median AQI",
    hover_name="State",
    hover_data={
        'State': True,
        'Median AQI': ':.0f',
        'Year': True},
    animation_frame="Year",
    scope="usa",
    title="Median AQI by County (2017-2023)",
    color_continuous_scale="Viridis"
)

# Save the choropleth map figure as an HTML file
choropleth_map_fig.write_html('/Users/clioluo/Desktop/Data Visualization/Final Project/choropleth_map.html')

# Create a Dash application
app = Dash(__name__, external_stylesheets=[dbc.themes.BOOTSTRAP])

app.layout = dbc.Container(
    [
        dbc.Row(
            dbc.Col(dcc.Graph(figure=choropleth_map_fig), width=12)
        ),
        dbc.Row(
            dbc.Col(dcc.Graph(figure=bubble_map_fig), width=12)
        )
    ],
    fluid=True
)

if __name__ == '__main__':
    app.run_server(debug=True)

Creating the combined map to show the changes in the relationship between the air quality and the fuel consumption for electricity generation.

In [5]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio

# Load CSV files for electric fuel consumption
file_paths = [
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2017.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2018.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2019.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2020.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2021.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2022.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2023.csv'
]

# Read CSV files into DataFrames
dfs = [pd.read_csv(file_path) for file_path in file_paths]

# Clean column names
dfs = [df.rename(columns=lambda x: x.strip().replace('\n', ' ')) for df in dfs]

# Convert 'Elec Fuel Consumption MMBtu' to numeric and aggregate by 'Plant State'
def clean_and_aggregate(df):
    df['Elec Fuel Consumption MMBtu'] = df['Elec Fuel Consumption MMBtu'].str.replace(',', '').astype(float)
    return df.groupby('Plant State')['Elec Fuel Consumption MMBtu'].sum().reset_index()

dfs = [clean_and_aggregate(df) for df in dfs]

# Add a year column to each DataFrame and combine all years into one data frame
for i, df in enumerate(dfs):
    df['Year'] = 2017 + i
combined_df = pd.concat(dfs, ignore_index=True)

# Ensure all state-year combinations are present, filling missing combinations with zero consumption
all_states = pd.Series(combined_df['Plant State'].unique())
all_years = pd.Series(range(2017, 2024))
state_year_df = pd.MultiIndex.from_product([all_states, all_years], names=['Plant State', 'Year']).to_frame(index=False)

combined_df_filled = state_year_df.merge(combined_df, on=['Plant State', 'Year'], how='left').fillna(0)
combined_df_filled['Elec Fuel Consumption MMBtu'] = combined_df_filled['Elec Fuel Consumption MMBtu'].astype(float)

# Load AQI data for each year (2017-2023)
files = {
    2017: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2017.csv',
    2018: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2018.csv',
    2019: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2019.csv',
    2020: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2020.csv',
    2021: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2021.csv',
    2022: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2022.csv',
    2023: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2023.csv'
}

# Read and prepare each dataset
aqi_dfs = []
for year, file_path in files.items():
    df = pd.read_csv(file_path)
    df = df[['State', 'County', 'Year', 'Median AQI']].rename(columns={'Median AQI': f'Median AQI {year}'})
    aqi_dfs.append(df)

# Merge all datasets on 'State' and 'County'
df_merged = aqi_dfs[0]
for df in aqi_dfs[1:]:
    df_merged = df_merged.merge(df, on=['State', 'County'], suffixes=('', '_drop'))
    df_merged.drop([col for col in df_merged.columns if 'drop' in col], axis=1, inplace=True)

# Mapping state names to their respective state abbreviations
state_abbrev = {
    'Alabama': 'AL', 'Alaska': 'AK', 'Arizona': 'AZ', 'Arkansas': 'AR',
    'California': 'CA', 'Colorado': 'CO', 'Connecticut': 'CT',
    'Delaware': 'DE', 'District Of Columbia': 'DC', 'Florida': 'FL',
    'Georgia': 'GA', 'Hawaii': 'HI', 'Idaho': 'ID', 'Illinois': 'IL',
    'Indiana': 'IN', 'Iowa': 'IA', 'Kansas': 'KS', 'Kentucky': 'KY',
    'Louisiana': 'LA', 'Maine': 'ME', 'Maryland': 'MD',
    'Massachusetts': 'MA', 'Michigan': 'MI', 'Minnesota': 'MN',
    'Mississippi': 'MS', 'Missouri': 'MO', 'Montana': 'MT',
    'Nebraska': 'NE', 'Nevada': 'NV', 'New Hampshire': 'NH',
    'New Jersey': 'NJ', 'New Mexico': 'NM', 'New York': 'NY',
    'North Carolina': 'NC', 'North Dakota': 'ND', 'Ohio': 'OH',
    'Oklahoma': 'OK', 'Oregon': 'OR', 'Pennsylvania': 'PA',
    'Rhode Island': 'RI', 'South Carolina': 'SC', 'South Dakota': 'SD',
    'Tennessee': 'TN', 'Texas': 'TX', 'Utah': 'UT', 'Vermont': 'VT',
    'Virginia': 'VA', 'Washington': 'WA', 'West Virginia': 'WV',
    'Wisconsin': 'WI', 'Wyoming': 'WY'
}

# Apply state abbreviation mapping
df_merged['State'] = df_merged['State'].map(state_abbrev)

# Combine the AQI data for animation
aqi_combined_df = pd.concat(
    [
        df_merged[['State', 'County', f'Median AQI {year}']].rename(columns={f'Median AQI {year}': 'Median AQI'}).assign(Year=year)
        for year in range(2017, 2024)
    ]
)

# Add electric fuel consumption to AQI data
merged_data = combined_df_filled.merge(aqi_combined_df, left_on=['Plant State', 'Year'], right_on=['State', 'Year'], how='inner')

# Create the figure
fig = go.Figure()

# Add AQI choropleth map
fig.add_trace(
    go.Choropleth(
        locations=aqi_combined_df['State'],
        z=aqi_combined_df['Median AQI'],
        locationmode='USA-states',
        colorscale='Viridis',
        marker_line_color='white',
        colorbar_title="Median AQI",
        zmin=aqi_combined_df['Median AQI'].min(),
        zmax=aqi_combined_df['Median AQI'].max()
    )
)

# Add electric fuel consumption bubbles
for year in range(2017, 2024):
    year_df = merged_data[merged_data['Year'] == year]
    
    fig.add_trace(
        go.Scattergeo(
            locationmode='USA-states',
            locations=year_df['Plant State'],
            text=year_df.apply(lambda row: f'State: {row["Plant State"]}<br>AQI: {row["Median AQI"]}<br>Fuel Consumption: {row["Elec Fuel Consumption MMBtu"]}', axis=1),
            marker=dict(
                size=year_df['Elec Fuel Consumption MMBtu'] / 2000000,  # Adjust the divisor to make bubbles smaller
                color='wheat',
                line_color='rgb(40,40,40)',
                line_width=0.5,
                sizemode='area',
                opacity=0.1 
            ),
            name=f'Year {year}',
            visible=(year == 2017)
        )
    )

# Update frames for animation
frames = [go.Frame(
    data=[
        go.Choropleth(
            locations=aqi_combined_df[aqi_combined_df['Year'] == year]['State'],
            z=aqi_combined_df[aqi_combined_df['Year'] == year]['Median AQI'],
            locationmode='USA-states',
            colorscale='Viridis',
            marker_line_color='white',
            zmin=aqi_combined_df['Median AQI'].min(),
            zmax=aqi_combined_df['Median AQI'].max()
        ),
        go.Scattergeo(
            locationmode='USA-states',
            locations=merged_data[merged_data['Year'] == year]['Plant State'],
            text=merged_data[merged_data['Year'] == year].apply(lambda row: f'State: {row["Plant State"]}<br>AQI: {row["Median AQI"]}<br>Fuel Consumption: {row["Elec Fuel Consumption MMBtu"]}', axis=1),
            marker=dict(
                size=merged_data[merged_data['Year'] == year]['Elec Fuel Consumption MMBtu'] / 2000000,  # Adjust the divisor to make bubbles smaller
                color='wheat',
                line_color='rgb(40,40,40)',
                line_width=0.5,
                sizemode='area',
                opacity=0.1 
            )
        )
    ],
    name=f'frame_{year}'
) for year in range(2017, 2024)]

# Add the frames to the figure
fig.frames = frames

# Define the slider steps
sliders = [dict(
    active=0,
    transition=dict(duration=300, easing='cubic-in-out'),
    steps=[dict(
        method='animate',
        args=[[f'frame_{year}'], dict(mode='immediate', frame=dict(duration=500, redraw=True), transition=dict(duration=0))],
        label=f'{year}'
    ) for year in range(2017, 2024)]
)]

# Layout settings for the figure
fig.update_layout(
    title_text='Median AQI by County and Fuel Consumption for Electric Generation by State (2017-2023)',
    geo=dict(
        scope='usa',
        projection=go.layout.geo.Projection(type='albers usa'),
        showlakes=True,
        lakecolor='rgb(255, 255, 255)',
    ),
    updatemenus=[dict(
        type='buttons',
        showactive=True,
        buttons=[dict(
            label='Play',
            method='animate',
            args=[None, dict(frame=dict(duration=1000, redraw=True), fromcurrent=True, transition=dict(duration=0))],
        )]
    )],
    sliders=sliders
)

# Save the figure as an HTML file
html_file_path = '/Users/clioluo/Desktop/Data Visualization/Final Project/output_map.html'
pio.write_html(fig, file=html_file_path, auto_open=True)

fig.show()

Changing the range of color bar to make the contrast more obvious.

In [6]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio

# Load CSV files for electric fuel consumption
file_paths = [
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2017.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2018.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2019.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2020.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2021.csv', 
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2022.csv',
    '/Users/clioluo/Desktop/Data Visualization/Final Project/Electric Fuel Consumption/2023.csv'
]

# Read CSV files into DataFrames
dfs = [pd.read_csv(file_path) for file_path in file_paths]

# Clean column names
dfs = [df.rename(columns=lambda x: x.strip().replace('\n', ' ')) for df in dfs]

# Convert 'Elec Fuel Consumption MMBtu' to numeric and aggregate by 'Plant State'
def clean_and_aggregate(df):
    df['Elec Fuel Consumption MMBtu'] = df['Elec Fuel Consumption MMBtu'].str.replace(',', '').astype(float)
    return df.groupby('Plant State')['Elec Fuel Consumption MMBtu'].sum().reset_index()

dfs = [clean_and_aggregate(df) for df in dfs]

# Add a year column to each DataFrame and combine all years into one data frame
for i, df in enumerate(dfs):
    df['Year'] = 2017 + i
combined_df = pd.concat(dfs, ignore_index=True)

# Ensure all state-year combinations are present, filling missing combinations with zero consumption
all_states = pd.Series(combined_df['Plant State'].unique())
all_years = pd.Series(range(2017, 2024))
state_year_df = pd.MultiIndex.from_product([all_states, all_years], names=['Plant State', 'Year']).to_frame(index=False)

combined_df_filled = state_year_df.merge(combined_df, on=['Plant State', 'Year'], how='left').fillna(0)
combined_df_filled['Elec Fuel Consumption MMBtu'] = combined_df_filled['Elec Fuel Consumption MMBtu'].astype(float)

# Load AQI data for each year (2017-2023)
files = {
    2017: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2017.csv',
    2018: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2018.csv',
    2019: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2019.csv',
    2020: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2020.csv',
    2021: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2021.csv',
    2022: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2022.csv',
    2023: '/Users/clioluo/Desktop/Data Visualization/Final Project/Air Quality/annual_aqi_by_county_2023.csv'
}

# Read and prepare each dataset
aqi_dfs = []
for year, file_path in files.items():
    df = pd.read_csv(file_path)
    df = df[['State', 'County', 'Year', 'Median AQI']].rename(columns={'Median AQI': f'Median AQI {year}'})
    aqi_dfs.append(df)

# Merge all datasets on 'State' and 'County'
df_merged = aqi_dfs[0]
for df in aqi_dfs[1:]:
    df_merged = df_merged.merge(df, on=['State', 'County'], suffixes=('', '_drop'))
    df_merged.drop([col for col in df_merged.columns if 'drop' in col], axis=1, inplace=True)

# Mapping state names to their respective state abbreviations
state_abbrev = {
    'Alabama': 'AL', 'Alaska': 'AK', 'Arizona': 'AZ', 'Arkansas': 'AR',
    'California': 'CA', 'Colorado': 'CO', 'Connecticut': 'CT',
    'Delaware': 'DE', 'District Of Columbia': 'DC', 'Florida': 'FL',
    'Georgia': 'GA', 'Hawaii': 'HI', 'Idaho': 'ID', 'Illinois': 'IL',
    'Indiana': 'IN', 'Iowa': 'IA', 'Kansas': 'KS', 'Kentucky': 'KY',
    'Louisiana': 'LA', 'Maine': 'ME', 'Maryland': 'MD',
    'Massachusetts': 'MA', 'Michigan': 'MI', 'Minnesota': 'MN',
    'Mississippi': 'MS', 'Missouri': 'MO', 'Montana': 'MT',
    'Nebraska': 'NE', 'Nevada': 'NV', 'New Hampshire': 'NH',
    'New Jersey': 'NJ', 'New Mexico': 'NM', 'New York': 'NY',
    'North Carolina': 'NC', 'North Dakota': 'ND', 'Ohio': 'OH',
    'Oklahoma': 'OK', 'Oregon': 'OR', 'Pennsylvania': 'PA',
    'Rhode Island': 'RI', 'South Carolina': 'SC', 'South Dakota': 'SD',
    'Tennessee': 'TN', 'Texas': 'TX', 'Utah': 'UT', 'Vermont': 'VT',
    'Virginia': 'VA', 'Washington': 'WA', 'West Virginia': 'WV',
    'Wisconsin': 'WI', 'Wyoming': 'WY'
}

# Apply state abbreviation mapping
df_merged['State'] = df_merged['State'].map(state_abbrev)

# Combine the AQI data for animation
aqi_combined_df = pd.concat(
    [
        df_merged[['State', 'County', f'Median AQI {year}']].rename(columns={f'Median AQI {year}': 'Median AQI'}).assign(Year=year)
        for year in range(2017, 2024)
    ]
)

# Add electric fuel consumption to AQI data
merged_data = combined_df_filled.merge(aqi_combined_df, left_on=['Plant State', 'Year'], right_on=['State', 'Year'], how='inner')

# Create the figure
fig = go.Figure()

# Add AQI choropleth map
fig.add_trace(
    go.Choropleth(
        locations=aqi_combined_df['State'],
        z=aqi_combined_df['Median AQI'],
        locationmode='USA-states',
        colorscale='Viridis',
        marker_line_color='white',
        colorbar_title="Median AQI",
        zmin=aqi_combined_df['Median AQI'].min(),
        zmax=100
    )
)

# Add electric fuel consumption bubbles
for year in range(2017, 2024):
    year_df = merged_data[merged_data['Year'] == year]
    
    fig.add_trace(
        go.Scattergeo(
            locationmode='USA-states',
            locations=year_df['Plant State'],
            text=year_df.apply(lambda row: f'State: {row["Plant State"]}<br>AQI: {row["Median AQI"]}<br>Fuel Consumption: {row["Elec Fuel Consumption MMBtu"]}', axis=1),
            marker=dict(
                size=year_df['Elec Fuel Consumption MMBtu'] / 2000000,  # Adjust the divisor to make bubbles smaller
                color='wheat',
                line_color='rgb(40,40,40)',
                line_width=0.5,
                sizemode='area',
                opacity=0.1 
            ),
            name=f'Year {year}',
            visible=(year == 2017)
        )
    )

# Update frames for animation
frames = [go.Frame(
    data=[
        go.Choropleth(
            locations=aqi_combined_df[aqi_combined_df['Year'] == year]['State'],
            z=aqi_combined_df[aqi_combined_df['Year'] == year]['Median AQI'],
            locationmode='USA-states',
            colorscale='Viridis',
            marker_line_color='white',
            zmin=aqi_combined_df['Median AQI'].min(),
            zmax=100
        ),
        go.Scattergeo(
            locationmode='USA-states',
            locations=merged_data[merged_data['Year'] == year]['Plant State'],
            text=merged_data[merged_data['Year'] == year].apply(lambda row: f'State: {row["Plant State"]}<br>AQI: {row["Median AQI"]}<br>Fuel Consumption: {row["Elec Fuel Consumption MMBtu"]}', axis=1),
            marker=dict(
                size=merged_data[merged_data['Year'] == year]['Elec Fuel Consumption MMBtu'] / 2000000,  # Adjust the divisor to make bubbles smaller
                color='wheat',
                line_color='rgb(40,40,40)',
                line_width=0.5,
                sizemode='area',
                opacity=0.1 
            )
        )
    ],
    name=f'frame_{year}'
) for year in range(2017, 2024)]

# Add the frames to the figure
fig.frames = frames

# Define the slider steps
sliders = [dict(
    active=0,
    transition=dict(duration=300, easing='cubic-in-out'),
    steps=[dict(
        method='animate',
        args=[[f'frame_{year}'], dict(mode='immediate', frame=dict(duration=500, redraw=True), transition=dict(duration=0))],
        label=f'{year}'
    ) for year in range(2017, 2024)]
)]

# Layout settings for the figure
fig.update_layout(
    title_text='Median AQI by County and Fuel Consumption for Electric Generation by State (2017-2023)',
    geo=dict(
        scope='usa',
        projection=go.layout.geo.Projection(type='albers usa'),
        showlakes=True,
        lakecolor='rgb(255, 255, 255)',
    ),
    updatemenus=[dict(
        type='buttons',
        showactive=True,
        buttons=[dict(
            label='Play',
            method='animate',
            args=[None, dict(frame=dict(duration=1000, redraw=True), fromcurrent=True, transition=dict(duration=0))],
        )]
    )],
    sliders=sliders
)

# Save the figure as an HTML file
html_file_path = '/Users/clioluo/Desktop/Data Visualization/Final Project/output_map.html'
pio.write_html(fig, file=html_file_path, auto_open=True)

fig.show()